# Machine Translation using OpenNMT

# Jamo and Char Tokenization

In [1]:
cd /home/ubuntu/MT

/home/ubuntu/MT


In [3]:
!pip install hgtk

Looking in indexes: http://ftp.daumkakao.com/pypi/simple
  Created wheel for hgtk: filename=hgtk-0.1.3-py2.py3-none-any.whl size=6689 sha256=c79e1449aa15b61035cead5f6ce27dcce6f4dc168f720c8444872605bbc5f22e
  Stored in directory: /home/ubuntu/.cache/pip/wheels/96/10/4b/0887dcaf5e0b0d26b807fef3497703fea2c44a76f91d198bd3
Successfully built hgtk


In [2]:
!python OpenNMT-py/tools/learn_bpe.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src.code -s 32000

In [4]:
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-morph.txt
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-morph.txt
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-morph.txt

In [3]:
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-bpe.txt

# **Preprocess the data**

We will be working with some example data in data/ folder.

The data consists of parallel source (src) and target (tgt) data containing one sentence per line with tokens separated by a space:

1. src-train.txt

2. tgt-train.txt

3. src-val.txt

4. tgt-val.txt


Train data and validataion data are required for machine translation training.

Validation files are required and used to evaluate the convergence of the training. It usually contains no more than 5000 sentences.


> If you think about it briefly, you can specify the path of train data and validation data, and specify the path and name to save in -save_data.

> If you want to set vocab size add below command
<br>
-src_vocab_size 32000 -tgt_vocab_size 32000

The vocab size is usually 32000.

In [1]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/bpe2bpe/demo -src_vocab_size -1 -tgt_vocab_size -1 -overwrite

[2020-12-11 05:48:04,269 INFO] Extracting features...
[2020-12-11 05:48:04,269 INFO]  * number of source features: 0.
[2020-12-11 05:48:04,269 INFO]  * number of target features: 0.
[2020-12-11 05:48:04,269 INFO] Building `Fields` object...
[2020-12-11 05:48:04,270 INFO] Building & saving training data...
[2020-12-11 05:48:08,101 INFO] Building shard 0.
[2020-12-11 05:49:13,440 INFO]  * saving 0th train data shard to OpenNMT-py/Data/bpe2bpe/demo.train.0.pt.
[2020-12-11 05:50:09,561 INFO]  * tgt vocab size: 32485.
[2020-12-11 05:50:09,730 INFO]  * src vocab size: 37015.
[2020-12-11 05:50:09,970 INFO] Building & saving validation data...
[2020-12-11 05:50:10,154 INFO] Building shard 0.
[2020-12-11 05:50:10,350 INFO]  * saving 0th valid data shard to OpenNMT-py/Data/bpe2bpe/demo.valid.0.pt.


!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

# **Train the data(Transformer)**

https://papers.nips.cc/paper/7181-attention-is-all-you-need.pdf


> If you get GPU-related errors, try halving batch_size

**Below is the full command, and if you want to know more about it, search about Transformer.**

!python OpenNMT-py/train.py -data OpenNMT-py/data/demo -save_model OpenNMT-py/data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 200000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

In [2]:
!nvidia-smi

Fri Dec 11 05:50:11 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64       Driver Version: 440.64       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Quadro RTX 6000     On   | 00000000:00:06.0 Off |                    0 |
| N/A   26C    P8    12W / 250W |      0MiB / 22698MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [3]:
!python OpenNMT-py/train.py -data OpenNMT-py/Data/bpe2bpe/demo -save_model OpenNMT-py/Data/bpe2bpe/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 50000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 10000 -world_size 1 -gpu_rank 0 -tensorboard -tensorboard_log_dir 'logs/my_board/bpe2bpe'

[2020-12-11 05:50:13,009 INFO]  * src vocab size = 37015
[2020-12-11 05:50:13,009 INFO]  * tgt vocab size = 32485
[2020-12-11 05:50:13,010 INFO] Building model...
[2020-12-11 05:50:20,765 INFO] NMTModel(
  (encoder): TransformerEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(37015, 512, padding_idx=1)
        )
        (pe): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (transformer): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_keys): Linear(in_features=512, out_features=512, bias=True)
          (linear_values): Linear(in_features=512, out_features=512, bias=True)
          (linear_query): Linear(in_features=512, out_features=512, bias=True)
          (softmax): Softmax(dim=-1)
          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_feat

[2020-12-11 05:50:20,862 INFO] Starting training on GPU: [0]
[2020-12-11 05:50:20,862 INFO] Start training loop and validate every 1000 steps...
[2020-12-11 05:50:20,863 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.train.0.pt
[2020-12-11 05:50:58,606 INFO] number of examples: 738178
[2020-12-11 05:51:30,059 INFO] Step 50/50000; acc:   3.49; ppl: 7412.96; xent: 8.91; lr: 0.00001; 4413/5691 tok/s;     69 sec
[2020-12-11 05:51:54,062 INFO] Step 100/50000; acc:   6.26; ppl: 5569.56; xent: 8.63; lr: 0.00001; 12749/16736 tok/s;     93 sec
[2020-12-11 05:52:18,400 INFO] Step 150/50000; acc:   6.17; ppl: 4241.16; xent: 8.35; lr: 0.00002; 12781/16542 tok/s;    118 sec
[2020-12-11 05:52:42,664 INFO] Step 200/50000; acc:   6.23; ppl: 2959.37; xent: 7.99; lr: 0.00002; 12811/16588 tok/s;    142 sec
[2020-12-11 05:53:06,999 INFO] Step 250/50000; acc:   6.42; ppl: 1960.16; xent: 7.58; lr: 0.00003; 12504/16634 tok/s;    166 sec
[2020-12-11 05:53:31,437 INFO] Step 300/50000; acc:   6.12; ppl

[2020-12-11 06:16:10,294 INFO] number of examples: 738178
[2020-12-11 06:16:35,590 INFO] Step 2900/50000; acc:  34.95; ppl: 33.67; xent: 3.52; lr: 0.00036; 3233/4237 tok/s;   1575 sec
[2020-12-11 06:16:59,922 INFO] Step 2950/50000; acc:  35.24; ppl: 32.81; xent: 3.49; lr: 0.00036; 12697/16269 tok/s;   1599 sec
[2020-12-11 06:17:24,287 INFO] Step 3000/50000; acc:  36.21; ppl: 30.13; xent: 3.41; lr: 0.00037; 12538/16544 tok/s;   1623 sec
[2020-12-11 06:17:24,290 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.valid.0.pt
[2020-12-11 06:17:24,725 INFO] number of examples: 8014
[2020-12-11 06:17:33,174 INFO] Validation perplexity: 39.4595
[2020-12-11 06:17:33,174 INFO] Validation accuracy: 38.2292
[2020-12-11 06:17:57,830 INFO] Step 3050/50000; acc:  36.38; ppl: 29.77; xent: 3.39; lr: 0.00038; 9289/11997 tok/s;   1657 sec
[2020-12-11 06:18:22,408 INFO] Step 3100/50000; acc:  36.98; ppl: 28.02; xent: 3.33; lr: 0.00038; 12619/16419 tok/s;   1682 sec
[2020-12-11 06:18:46,751 INFO] Step

[2020-12-11 06:40:55,612 INFO] number of examples: 738178
[2020-12-11 06:41:08,412 INFO] Step 5750/50000; acc:  51.95; ppl:  9.07; xent: 2.21; lr: 0.00071; 3555/4688 tok/s;   3048 sec
[2020-12-11 06:41:32,427 INFO] Step 5800/50000; acc:  51.65; ppl:  9.24; xent: 2.22; lr: 0.00072; 12720/16433 tok/s;   3072 sec
[2020-12-11 06:41:56,582 INFO] Step 5850/50000; acc:  52.48; ppl:  8.76; xent: 2.17; lr: 0.00072; 12632/16640 tok/s;   3096 sec
[2020-12-11 06:42:21,156 INFO] Step 5900/50000; acc:  51.65; ppl:  9.18; xent: 2.22; lr: 0.00073; 12810/16364 tok/s;   3120 sec
[2020-12-11 06:42:45,458 INFO] Step 5950/50000; acc:  52.86; ppl:  8.53; xent: 2.14; lr: 0.00074; 12669/16581 tok/s;   3145 sec
[2020-12-11 06:43:09,697 INFO] Step 6000/50000; acc:  52.92; ppl:  8.54; xent: 2.15; lr: 0.00074; 12657/16677 tok/s;   3169 sec
[2020-12-11 06:43:09,698 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.valid.0.pt
[2020-12-11 06:43:10,049 INFO] number of examples: 8014
[2020-12-11 06:43:18,483 INF

[2020-12-11 07:04:43,989 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.train.0.pt
[2020-12-11 07:05:36,179 INFO] number of examples: 738178
[2020-12-11 07:06:02,827 INFO] Step 8650/50000; acc:  57.24; ppl:  6.39; xent: 1.85; lr: 0.00095; 3506/4526 tok/s;   4542 sec
[2020-12-11 07:06:26,980 INFO] Step 8700/50000; acc:  56.94; ppl:  6.51; xent: 1.87; lr: 0.00095; 12851/16493 tok/s;   4566 sec
[2020-12-11 07:06:51,054 INFO] Step 8750/50000; acc:  58.27; ppl:  6.04; xent: 1.80; lr: 0.00094; 12645/16765 tok/s;   4590 sec
[2020-12-11 07:07:15,324 INFO] Step 8800/50000; acc:  57.70; ppl:  6.22; xent: 1.83; lr: 0.00094; 12766/16586 tok/s;   4614 sec
[2020-12-11 07:07:39,650 INFO] Step 8850/50000; acc:  58.02; ppl:  6.10; xent: 1.81; lr: 0.00094; 12816/16640 tok/s;   4639 sec
[2020-12-11 07:08:03,830 INFO] Step 8900/50000; acc:  58.42; ppl:  5.99; xent: 1.79; lr: 0.00094; 12797/16605 tok/s;   4663 sec
[2020-12-11 07:08:28,048 INFO] Step 8950/50000; acc:  58.33; ppl:  5.98; xent: 1.79;

...

[2020-12-11 11:09:57,656 INFO] Step 37100/50000; acc:  74.27; ppl:  2.66; xent: 0.98; lr: 0.00046; 12412/16276 tok/s;  19177 sec
[2020-12-11 11:10:22,094 INFO] Step 37150/50000; acc:  74.27; ppl:  2.67; xent: 0.98; lr: 0.00046; 12586/16069 tok/s;  19201 sec
[2020-12-11 11:10:46,564 INFO] Step 37200/50000; acc:  74.25; ppl:  2.66; xent: 0.98; lr: 0.00046; 12238/16044 tok/s;  19226 sec
[2020-12-11 11:11:10,586 INFO] Step 37250/50000; acc:  74.38; ppl:  2.64; xent: 0.97; lr: 0.00046; 12306/16375 tok/s;  19250 sec
[2020-12-11 11:11:34,896 INFO] Step 37300/50000; acc:  74.28; ppl:  2.63; xent: 0.97; lr: 0.00046; 12448/16064 tok/s;  19274 sec
[2020-12-11 11:11:52,572 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.train.0.pt
[2020-12-11 11:12:38,679 INFO] number of examples: 738178
[2020-12-11 11:12:55,079 INFO] Step 37350/50000; acc:  74.00; ppl:  2.68; xent: 0.99; lr: 0.00046; 3775/4956 tok/s;  19354 sec
[2020-12-11 11:13:19,167 INFO] Step 37400/50000; acc:  74.19; ppl:  2.67; xent

[2020-12-11 11:34:45,326 INFO] number of examples: 8014
[2020-12-11 11:34:53,872 INFO] Validation perplexity: 4.30637
[2020-12-11 11:34:53,872 INFO] Validation accuracy: 67.8166
[2020-12-11 11:34:54,156 INFO] Saving checkpoint OpenNMT-py/Data/bpe2bpe/model/model_step_40000.pt
[2020-12-11 11:35:24,070 INFO] Step 40050/50000; acc:  74.80; ppl:  2.61; xent: 0.96; lr: 0.00044; 7806/9970 tok/s;  20703 sec
[2020-12-11 11:35:48,298 INFO] Step 40100/50000; acc:  74.84; ppl:  2.58; xent: 0.95; lr: 0.00044; 12159/16147 tok/s;  20727 sec
[2020-12-11 11:36:12,471 INFO] Step 40150/50000; acc:  75.06; ppl:  2.57; xent: 0.95; lr: 0.00044; 12445/16163 tok/s;  20752 sec
[2020-12-11 11:36:36,639 INFO] Step 40200/50000; acc:  74.96; ppl:  2.59; xent: 0.95; lr: 0.00044; 12565/16354 tok/s;  20776 sec
[2020-12-11 11:36:40,679 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.train.0.pt
[2020-12-11 11:37:31,491 INFO] number of examples: 738178
[2020-12-11 11:38:02,399 INFO] Step 40250/50000; acc:  74.5

[2020-12-11 11:59:48,836 INFO] Step 42900/50000; acc:  75.54; ppl:  2.53; xent: 0.93; lr: 0.00043; 12604/16198 tok/s;  22168 sec
[2020-12-11 12:00:13,205 INFO] Step 42950/50000; acc:  75.43; ppl:  2.53; xent: 0.93; lr: 0.00043; 12182/16095 tok/s;  22192 sec
[2020-12-11 12:00:37,278 INFO] Step 43000/50000; acc:  75.54; ppl:  2.52; xent: 0.92; lr: 0.00043; 12342/16401 tok/s;  22216 sec
[2020-12-11 12:00:37,281 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.valid.0.pt
[2020-12-11 12:00:37,725 INFO] number of examples: 8014
[2020-12-11 12:00:46,141 INFO] Validation perplexity: 4.29357
[2020-12-11 12:00:46,141 INFO] Validation accuracy: 67.9535
[2020-12-11 12:01:10,557 INFO] Step 43050/50000; acc:  75.39; ppl:  2.53; xent: 0.93; lr: 0.00043; 9120/11728 tok/s;  22250 sec
[2020-12-11 12:01:25,261 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.train.0.pt
[2020-12-11 12:02:16,107 INFO] number of examples: 738178
[2020-12-11 12:02:34,867 INFO] Step 43100/50000; acc:  75.26; ppl

[2020-12-11 12:24:15,063 INFO] Step 45750/50000; acc:  75.81; ppl:  2.49; xent: 0.91; lr: 0.00041; 12488/16165 tok/s;  23634 sec
[2020-12-11 12:24:39,418 INFO] Step 45800/50000; acc:  75.93; ppl:  2.49; xent: 0.91; lr: 0.00041; 12417/16074 tok/s;  23659 sec
[2020-12-11 12:25:03,651 INFO] Step 45850/50000; acc:  75.90; ppl:  2.47; xent: 0.91; lr: 0.00041; 12380/16289 tok/s;  23683 sec
[2020-12-11 12:25:27,848 INFO] Step 45900/50000; acc:  76.20; ppl:  2.46; xent: 0.90; lr: 0.00041; 12377/16104 tok/s;  23707 sec
[2020-12-11 12:25:52,107 INFO] Step 45950/50000; acc:  75.88; ppl:  2.48; xent: 0.91; lr: 0.00041; 12604/16360 tok/s;  23731 sec
[2020-12-11 12:25:53,200 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.train.0.pt
[2020-12-11 12:26:33,697 INFO] number of examples: 738178
[2020-12-11 12:27:07,004 INFO] Step 46000/50000; acc:  75.72; ppl:  2.50; xent: 0.92; lr: 0.00041; 4062/5256 tok/s;  23806 sec
[2020-12-11 12:27:07,006 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/de

[2020-12-11 12:48:39,934 INFO] Step 48600/50000; acc:  76.28; ppl:  2.44; xent: 0.89; lr: 0.00040; 12545/16391 tok/s;  25099 sec
[2020-12-11 12:49:04,066 INFO] Step 48650/50000; acc:  76.59; ppl:  2.43; xent: 0.89; lr: 0.00040; 12558/16187 tok/s;  25123 sec
[2020-12-11 12:49:28,330 INFO] Step 48700/50000; acc:  76.49; ppl:  2.43; xent: 0.89; lr: 0.00040; 12311/16205 tok/s;  25147 sec
[2020-12-11 12:49:52,400 INFO] Step 48750/50000; acc:  76.48; ppl:  2.43; xent: 0.89; lr: 0.00040; 12344/16339 tok/s;  25172 sec
[2020-12-11 12:50:16,668 INFO] Step 48800/50000; acc:  76.43; ppl:  2.43; xent: 0.89; lr: 0.00040; 12487/16120 tok/s;  25196 sec
[2020-12-11 12:50:29,032 INFO] Loading dataset from OpenNMT-py/Data/bpe2bpe/demo.train.0.pt
[2020-12-11 12:51:26,744 INFO] number of examples: 738178
[2020-12-11 12:51:49,026 INFO] Step 48850/50000; acc:  76.40; ppl:  2.44; xent: 0.89; lr: 0.00040; 3301/4311 tok/s;  25288 sec
[2020-12-11 12:52:13,220 INFO] Step 48900/50000; acc:  76.28; ppl:  2.45; xent

# **Translate**

Now that you have your model, you can start translating.

-model ==> Setting your model

Output predictions into pred.txt

In [24]:
!python OpenNMT-py/translate.py -model OpenNMT-py/Data/bpe2bpe/model/model_step_50000.pt -src OpenNMT-py/Data/src-test-bpe.txt -output OpenNMT-py/Data/bpe2bpe/pred_50k.txt -replace_unk -verbose -beam_size 1 -gpu 0

[2020-12-11 18:45:02,131 INFO] Translating shard 0.
[2020-12-11 18:45:02,989 INFO] 
SENT 1: ['"@@', '경찰의', '설명을', '보면,', '손님@@', '으로', '피@@', '시@@', '방을', '찾은', '김씨는', '다른', '손님이', '남긴', '음식@@', '물을', '자리에서', '치@@', '워@@', '달라는', '요구를', '하다', '신@@', '씨와', '말@@', '다툼을', '했다고', '한다."']
PRED 1: "According to the police, Kim, who visited the PC room as a gu@@ est, had an argument with Shin while demanding that the food left by another guest be removed from his seat."
PRED SCORE: -0.0906

[2020-12-11 18:45:02,989 INFO] 
SENT 2: ['잠실@@', '여자@@', '고등학교@@', '(@@', '교장', '김인@@', '봉@@', ')는', '실@@', '력과', '인@@', '성을', '갖춘', '인재를', '기@@', '른@@', '다는', '지향@@', '점을', '가지고', '교사와', '학생이', '‘@@', '신뢰@@', '의', '팀@@', '플레이@@', '’를', '통해', '진로@@', '진학', '프로그램을', '업그레이드@@', '해', '나가고', '있다.']
PRED 2: Jamsil Girls' High School (@@ Principal Kim In-@@ bong@@ ) is upgraded to a career advancement program through '@@ Team Play of Tru@@ st@@ ' by teachers and students with the goal of raising talented people 

[2020-12-11 18:45:03,593 INFO] 
SENT 31: ['"@@', '단독', '콘서트', '무대가', '아닌,', '주', '시청@@', '층이', '청소년@@', '들인', '시상식', '무대@@', '였다는', '점에서', '화@@', '사의', '의@@', '상', '선택@@', '에는', '아쉬움이', '남@@', '는다."']
PRED 31: "Given that the main audience was not a solo concert stage, but an award ceremony for teenagers, it is regrettable to choose Hwas@@ a's costum@@ e."
PRED SCORE: -0.0847

[2020-12-11 18:45:03,593 INFO] 
SENT 32: ['"@@', '추가', '취업', '희망@@', '자@@', '에다', '구직@@', '단@@', '념@@', '자,', '취업준비@@', '자', '등을', '합친', '청년@@', '층의', '잠재@@', '실업@@', '률은', '23@@', '%에', '달해', '청년', '4명', '가운데', '한', '명이', '실질적인', '실업', '상태에', '놓여', '있는', '상황이다."']
PRED 32: "In addition to the prospective job seek@@ ers, the potential unemployment rate of young people, which includes job seekers and job seek@@ ers, reached 23@@ %, with one out of four young people at a real unemployment situation."
PRED SCORE: -0.0886

[2020-12-11 18:45:03,594 INFO] 
SENT 33: ['지역@@', '산업', '활력', '회복을', '위한', '단기@@', '일자리', '대책이'

[2020-12-11 18:45:04,202 INFO] 
SENT 61: ['이와', '달리', '우@@', '기에는', '목@@', '초가', '무성@@', '해', '구@@', '충@@', '제와', '항생@@', '제의', '수요가', '높다.']
PRED 61: "In contrast, there are many woo@@ ds in the rainy season, so the demand for insec@@ tic@@ ide and anti@@ biotics is high."
PRED SCORE: -0.0809

[2020-12-11 18:45:04,202 INFO] 
SENT 62: ['대전@@', '지역', '경제가', '흔들리고', '있다는', '통계가', '지난해부터', '연이어', '나오고', '있다.']
PRED 62: Statistics have been coming out since last year that the economy of Daejeon is shak@@ ing.
PRED SCORE: -0.0796

[2020-12-11 18:45:04,203 INFO] 
SENT 63: ['"남@@', '측에서는', '조용@@', '근', '육군@@', '대@@', '령@@', '과', '관련', '실무@@', '담당@@', '관', '등', '총', '4명@@', '이,', '북@@', '측에서는', '엄@@', '창@@', '남', '육군@@', '대@@', '좌@@', '와', '관련', '실무@@', '담당@@', '관', '등', '총', '4명이', '각각', '참석했다."']
PRED 63: "A total of four people from the South, including Army Colonel Cho Yong-@@ geun and related working-level officials, and from the North, a total of four people from the South, including Arm

[2020-12-11 18:45:04,206 INFO] 
SENT 86: ['"과거', '이@@', '매@@', '리는', 'S', '모', '방송@@', '국', '작품에', '출연@@', '이', '확정@@', ',', '담당', '캐릭터를', '위해', '연습@@', '에', '매진@@', '했으나', '갑작스럽게', '스케@@', '줄이', '연기@@', '되며', '촬영이', '중단@@', '됐다."']
PRED 86: "In the past, Lee M@@ ae-@@ ri was confirmed to appear in a TV show work and focused on practicing for the character in charge, but the shooting was suspended due to a sudden delay in his schedule."
PRED SCORE: -0.0788

[2020-12-11 18:45:04,206 INFO] 
SENT 87: ['그', '종교', '안에', '담긴', '진@@', '리를', '들여다@@', '볼', '여지를', '주지', '않고', '그', '종교@@', '가', '지시@@', '하는', '참', '가치와', '만날', '기회를', '차단@@', '한다.']
PRED 87: "Instead of giving room for looking into the truth contained in the religion, it blocks the opportunity to meet the true value ordered by the religi@@ on."
PRED SCORE: -0.0857

[2020-12-11 18:45:04,206 INFO] 
SENT 88: ['내가', '사역@@', '했@@', '었던', '대부분의', '교회@@', '들에게', '선교@@', '사@@', '역은', '매우', '중요한', '목표@@', '와', '비전@@', '이었다.']
PRED 88: "For 

[2020-12-11 18:45:05,225 INFO] 
SENT 121: ['그', '과정에서', '가장', '중시하는', '것은', '만@@', '화의', '특별한', '예술@@', '성에', '만화@@', '가@@', '뿐', '아니라', '모든', '국민이', '함께', '참여할', '수', '있도록', '하는', '것이다.']
PRED 121: The most important thing in the process is not only the carto@@ ons but also the way that all the people can participate together in the special arti@@ stry of carto@@ ons.
PRED SCORE: -0.0779

[2020-12-11 18:45:05,225 INFO] 
SENT 122: ['"부산@@', '과', '대구@@', '도', '각각', '76@@', '%와', '7@@', '2.9@@', '%로', '높은', '반면,', '세종@@', '은', '20@@', '.0@@', '%로', '외@@', '지인의', '토지@@', '소유', '비중이', '높은', '것으로', '나타났다."']
PRED 122: "Busan and Daegu also have a high rate of 7@@ 6% and 7@@ 2.@@ 9%, respectively, while Sejong had 20.@@ 0@@ %, which is a high proportion of foreign acquaint@@ ance's land owner@@ ship."
PRED SCORE: -0.0860

[2020-12-11 18:45:05,226 INFO] 
SENT 123: ['"무@@', '차별@@', '적', '테러', '공격@@', '과', '잔@@', '혹한', '공개@@', '처@@', '형,', '자극@@', '적인', '홍보', '같은', 'IS@@', '식', '활동은', '지@@', '양

...

[2020-12-11 18:47:46,966 INFO] 
SENT 7891: ['그중', '하나가', '도시@@', '계획을', '통한', '공동체', '조성과', '공유@@', '가치', '실현@@', '이다.']
PRED 7891: One of them is the creation of a community through urban plans and the realization of shared value.
PRED SCORE: -0.0822

[2020-12-11 18:47:46,966 INFO] 
SENT 7892: ['모든', '멤버가', '10@@', '대로', '구성된', '6@@', '인@@', '조', '그룹', '‘더', '이@@', '스트', '라이트@@', '’', '폭행', '사건의', '철저한', '수사를', '촉구하는', '국민청원', '동의', '수가', '청와대', '답변', '기준인', '20만@@', '명을', '넘어섰다.']
PRED 7892: "The number of petitions calling for a thorough investigation into the six-@@ member group ""The East Light@@ "" assault case, which consists of 10 members, exceeded 200,000 people, the standard for the Blue House's response."
PRED SCORE: -0.0896

[2020-12-11 18:47:46,966 INFO] 
SENT 7893: ['점유율', '1위인', '신라@@', '면이', '이', '같은', '변화에', '직격탄을', '맞@@', '았다는', '해석@@', '이다.']
PRED 7893: "Analysts say that Shin Ram@@ yun, the No. 1 player in the market share, was directly hit by such changes."
PRED SC

[2020-12-11 18:47:47,566 INFO] 
SENT 7921: ['권@@', '용수', '주@@', '우즈베키스탄', '대사는', '“@@', '스마트@@', '미터', '프로젝트의', '성공', '추진을', '바탕으로', 'KT@@', '의', '우즈@@', '벡', '사업이', '다양한', 'ICT', '분야로', '확대@@', '돼', '나가@@', '기를', '바란다”고', '밝혔다.']
PRED 7921: """We hope KT's business in Uzbekistan will expand to various ICT sectors based on the success of the smart meter project@@ ,"" said Kwon Yong-@@ soo, ambassador to Uzbek@@ ist@@ an."
PRED SCORE: -0.0786

[2020-12-11 18:47:47,566 INFO] 
SENT 7922: ['펑@@', '샨@@', '샨@@', '의', '뒤를', '이@@', '을', '중국', '여자', '골프@@', '의', '미래@@', '로', '불리는', '수@@', '이@@', '샹@@', '은', '특히', '쇼트@@', '게임', '능력이', '뛰@@', '나@@', '다는', '평가를', '받는다.']
PRED 7922: "Su@@ i@@ cham@@ p, who is called the future of Chinese women's golf that will succeed F@@ eng@@ sh@@ an Shan@@ sh@@ an, is considered to be particularly capable of short games."
PRED SCORE: -0.0879

[2020-12-11 18:47:47,566 INFO] 
SENT 7923: ['영어가', '정규', '교과@@', '로', '편성@@', '되는', '것은', '초등학교', '3@@', '학년@@', '부터다.']


[2020-12-11 18:47:48,257 INFO] 
SENT 7951: ['카타@@', '르는', '4@@', '경기@@', '서', '10@@', '골을', '허용@@', '했을', '정도로', '수비가', '약한', '팀@@', '이기', '때문에', '정상적으로', '상대@@', '하면', '충분히', '이길', '수', '있는', '상대@@', '다.']
PRED 7951: "@@ Qatar is a weak team with fewer defensive skills, allowing 10 goals in four matches, so if they deal with it norm@@ ally, they can win enough."
PRED SCORE: -0.0839

[2020-12-11 18:47:48,257 INFO] 
SENT 7952: ['대상@@', '㈜@@', '에서', '제조@@', '한', '청정@@', '원', '‘@@', '런@@', '천@@', '미@@', '트@@', '’의', '일부', '제품에서', '세균이', '검출@@', '돼', '식품의약품안전@@', '처@@', '로부터', '판매', '중단', '및', '회수@@', '조치', '판정을', '받았다.']
PRED 7952: "B@@ er@@ dro@@ pers were detected in some of the products of the clean@@ er's ""R@@ un@@ cheon Me@@ at@@ "" manufactured by Daes@@ ang Corporation, and were declared to be suspended and recovered from the Ministry of Food and Drug Saf@@ ety."
PRED SCORE: -0.0832

[2020-12-11 18:47:48,257 INFO] 
SENT 7953: ['"강@@', '씨', '등은', '김씨가', '휴대전화', '가@@', '개통', '이후', '

[2020-12-11 18:47:48,796 INFO] 
SENT 7981: ['"@@', '근대@@', '건축물', '기록@@', '보존@@', '사업은', '지난', '2010년부터', '광주시가', '추진하고', '있는', '사업@@', '으로,', '그동안', '사업@@', '대상', '건물@@', '주의', '비@@', '협조@@', '와', '건축물', '산@@', '재로', '사업@@', '추진에', '적지', '않은', '어려움을', '겪@@', '었다."']
PRED 7981: "The modern building record conservation project has been promoted by Gwangju since 2010, and it has been difficult to promote the project due to the non-@@ cooperation of the building owners subject to the project and the construction of buildings."
PRED SCORE: -0.0845

[2020-12-11 18:47:48,797 INFO] 
SENT 7982: ['보도에', '따르면', '방', '전', '대표', '주변@@', '인들은', '방', '전', '대표가', '장', '씨와', '2008@@', '년@@', '∼@@', '2009@@', '년에', '잠시', '동안', '자주', '만나는', '사이@@', '였으며', '방', '대표가', '장', '씨를', '언급@@', '하기도', '했다고', '진술했다.']
PRED 7982: "According to reports, the former representative Bang stated that Bang had been meeting Jang for a while between 2008 and 2009, and CEO Bang also mentioned Jang@@ ."
PRED SCORE: -0.0870



[2020-12-11 18:47:49,230 INFO] 
SENT 8011: ['다만', '북미가', '공동', '유해@@', '발굴', '사업에', '합의@@', '한다면', '미국', '장비@@', '의', '대북', '반입@@', '과', '발굴', '비용', '지@@', '불', '등을', '위한', '대북제재', '예외', '인@@', '정이', '필요하다.']
PRED 8011: "However, if North Korea and the U.S. agree on a joint project to excav@@ ate the remains, it is necessary to recognize exceptions to the sanctions against North Korea to bring in U.S. equipment to North Korea and pay for the excav@@ ation."
PRED SCORE: -0.0861

[2020-12-11 18:47:49,230 INFO] 
SENT 8012: ['출산@@', '과', '육아@@', '에', '대한', '부담이', '부모에게', '지나치게', '쏠리는', '환경을', '개선@@', '하지', '않으면', '저출산', '문제를', '해결하는', '건', '요원@@', '하다.']
PRED 8012: It is a long way to solve the problem of low birth rate unless the government improves an environment where the burden of childbirth and childcare is excessively concentrated on parents.
PRED SCORE: -0.0842

[2020-12-11 18:47:49,231 INFO] 
SENT 8013: ['여기', '국내', '론@@', '칭', '이후', '누적@@', '판매', '10만@@', '대를', '돌파한', '유모@@', '차가'


# Detokenization

Even after the translation process is finished, it is still in a segment, so it is different from the actual sentence structure used by real people. Thus, when you perform a detoxification process, it is returned in the form of the actual sentence.

We Use "sed" for BPE Detokenization


In [25]:
!sed -i "s/@@ //g"  OpenNMT-py/Data/bpe2bpe/pred_50k.txt

# Post-processing

In [ ]:
f = open('OpenNMT-py/Data/tgt-test-char.txt', 'r', encoding='utf-8')
txt = f.read()
txt = txt.replace(' ', '')
txt = txt.replace('ᴥ', ' ')

with open("OpenNMT-py/Data/tgt-test-char1.txt", "w") as f:
    f.write(txt)
    


In [16]:
# f = open('OpenNMT-py/Data/bpe2bpe/pred_10k.txt', 'r', encoding='utf-8')
# txt = f.read()
# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

# with open("OpenNMT-py/Data/bpe2bpe/pred_10k-edited.txt", "w") as f:
#     f.write(txt)

f = open('OpenNMT-py/Data/bpe2bpe/pred_20k.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'"According to the explanation of the police, Kim, who visited the PC room as a guest, reportedly had an argument with Shin while demanding that the food left by another guest be removed from the seat."\nJamsil Girls\' High School (Principal Kim In-bong) has upgraded its career path program through \'Trust Team Play\' with the goal of fostering talented people with skills and talent.\n"If the sentence of more than 1 million won is confirmed, former lawmaker Kim will lose his right to vote and his right to vote for five years."\n"The working environment of Daejeon Industrial Complex, Daehwa-dong, Daedeok-gu, Daejeon City will be improved."\n"At the TV-wave construction site of Wei Port in Namwon-eup, Seogui-po-si was lost in waves with a high reinforcement facility of about 90 tons, and the central divider was reduced to 100 meters in the section of the Nohyeong Rotter-Samsung Service Center in Jeju."\nIt is a program to make students value physical and art.\n"The U.S. Justice Departmen

# Evaluation Using BLEU

Quantitative evaluation is performed on the sentence thus obtained. BLEU is a quantitative evaluation method for machine translation. You can see which model is superior by comparing it to the BLEU score you are comparing.

https://www.aclweb.org/anthology/P02-1040

In [26]:
!perl  OpenNMT-py/tools/multi-bleu.perl OpenNMT-py/Data/tgt-test.txt < OpenNMT-py/Data/bpe2bpe/pred_50k.txt

BLEU = 23.54, 51.1/28.9/18.0/11.6 (BP=0.999, ratio=0.999, hyp_len=227063, ref_len=227303)
